# Value gradient error for linear policies in LQG

Experiment description on [Overleaf](https://www.overleaf.com/read/cmbgmxxpxqzr).

**Versioning:** [CalVer](https://calver.org) `MM.DD.MICRO`

In [1]:
from __future__ import annotations

import logging
import os
import os.path as osp

import lqsvg
import lqsvg.envs.lqr.utils as lqg_util
import lqsvg.experiment.utils as utils
import lqsvg.torch.named as nt
import pytorch_lightning as pl
import ray
import wandb
from lqsvg.experiment.data import build_datamodule
from lqsvg.experiment.models import LightningModel
from lqsvg.experiment.worker import make_worker
from ray import tune
from raylab.policy.model_based.lightning import LightningTrainerSpec
from torch import Tensor

In [2]:
class InputStatistics(pl.callbacks.Callback):
    def on_train_batch_end(
        self,
        trainer: pl.Trainer,
        pl_module: pl.LightningModule,
        outputs: Tensor,
        batch: tuple[Tensor, Tensor, Tensor],
        batch_idx: int,
        dataloader_idx: int,
    ):
        del trainer, outputs, batch_idx, dataloader_idx
        obs, act, new_obs = batch
        pl_module.log("train/obs-mean", obs.mean())
        pl_module.log("train/obs-std", obs.std())
        pl_module.log("train/act-mean", act.mean())
        pl_module.log("train/act-std", act.std())
        pl_module.log("train/new_obs-mean", new_obs.mean())
        pl_module.log("train/new_obs-std", new_obs.std())

In [3]:
class Experiment(tune.Trainable):
    def setup(self, config: dict):
        os.environ["WANDB_SILENT"] = "true"
        cwd = config.pop("wandb_dir")
        self.run = wandb.init(
            dir=cwd,
            name="SVG Prediction",
            config=config,
            project="LQG-SVG",
            entity="angelovtt",
            tags=[utils.calver()],
            reinit=True,
            mode="offline",
            save_code=True,
        )

        self.make_worker()
        self.make_model()
        self.make_datamodule()
        self.make_lightning_trainer()
        #         self.make_artifact()
        utils.suppress_lightning_info_logging()

    @property
    def hparams(self):
        return self.run.config

    def make_worker(self):
        with nt.suppress_named_tensor_warning():
            self.worker = make_worker(
                env_config=self.hparams.env_config,
                # TorchPolicy internally pulls the 'policy' key from config
                policy_config=dict(self.hparams),
                log_level=logging.WARNING,
            )

    def make_model(self):
        self.model = LightningModel(self.worker.get_policy(), self.worker.env)
        self.model.hparams.learning_rate = self.hparams.learning_rate
        self.model.hparams.mc_samples = self.hparams.mc_samples
        self.model.hparams.weight_decay = self.hparams.weight_decay

    def make_datamodule(self):
        self.datamodule = build_datamodule(
            self.worker, total_trajs=self.hparams.total_trajs
        )
        self.datamodule.collect_trajectories(prog=False)

    def make_lightning_trainer(self):
        logger = pl.loggers.WandbLogger(
            save_dir=self.run.dir, log_model=False, experiment=self.run
        )

        early_stopping = pl.callbacks.EarlyStopping(
            monitor=LightningModel.early_stop_on,
            min_delta=float(self.hparams.improvement_delta),
            patience=int(self.hparams.patience),
            mode="min",
            strict=True,
        )
        #         checkpointing = pl.callbacks.ModelCheckpoint(
        #             dirpath=osp.join(self.run.dir, "checkpoints"),
        #             monitor=LightningModel.early_stop_on,
        #             save_top_k=-1,
        #             period=10,
        #             save_last=True,
        #         )
        self.trainer = pl.Trainer(
            default_root_dir=self.run.dir,
            logger=logger,
            num_sanity_val_steps=2,
            #             callbacks=[early_stopping, checkpointing, InputStatistics()],
            callbacks=[early_stopping, InputStatistics()],
            max_epochs=self.hparams.max_epochs,
            progress_bar_refresh_rate=0,  # don't show progress bar for model training
            weights_summary=None,  # don't print summary before training
        )

    def make_artifact(self):
        env = self.worker.env
        self.artifact = wandb.Artifact(
            f"svg_prediction-lqg{env.n_state}.{env.n_ctrl}.{env.horizon}", type="model"
        )

    def step(self) -> dict:
        self.log_env_info()
        with utils.suppress_dataloader_warning():
            self.trainer.fit(self.model, datamodule=self.datamodule)

            results = self.trainer.test(self.model, datamodule=self.datamodule)[0]
            self.run.summary.update(results)

        #         try:
        #             self.artifact.add_dir(self.trainer.checkpoint_callback.dirpath)
        #             self.run.log_artifact(self.artifact)
        #         except ValueError:
        #             # Sometimes add_dir fails with 'not a directory name'. Shall investigate
        #             pass
        return {tune.result.DONE: True, **results}

    def log_env_info(self):
        dynamics = self.worker.env.dynamics
        eigvals = lqg_util.stationary_eigvals(dynamics)
        tests = {
            "stability": lqg_util.isstable(eigvals=eigvals),
            "controllability": lqg_util.iscontrollable(dynamics),
        }
        self.run.summary.update(tests)
        self.run.summary.update({"Fs_eigvals": wandb.Histogram(eigvals)})

    def cleanup(self):
        self.run.finish()

In [4]:
ray.init(logging_level=logging.WARNING)
lqsvg.register_all()
utils.suppress_lightning_info_logging()

config = {
    "wandb_dir": os.getcwd(),
    "env_config": dict(
        n_state=tune.randint(2, 11),
        n_ctrl=tune.randint(2, 11),
        horizon=tune.randint(1, 200),
        stationary=True,
        Fs_eigval_range=(0.0, 1.0),
        transition_bias=False,
        rand_trans_cov=True,
        rand_init_cov=False,
        cost_linear=tune.choice([True, False]),
        cost_cross=tune.choice([True, False]),
        num_envs=100,
    ),
    "policy": {
        "module": {
            "policy_initializer": "xavier_uniform",
            "model_initializer": "xavier_uniform",
            "stationary_model": True,
            "residual_model": tune.choice([True, False]),
            "model_input_norm": None,
        }
    },
    "learning_rate": tune.loguniform(1e-4, 1e-2),
    "weight_decay": tune.loguniform(1e-5, 1e-3),
    "mc_samples": 32,
    "total_trajs": 1000,
    "improvement_delta": 0.0,
    "patience": 3,
    "max_epochs": 1000,
}

analysis = tune.run(Experiment, config=config, num_samples=256, local_dir="./results")

(pid=2527) 2021-03-29 09:51:14,939	WARNING deprecation.py:33 -- DeprecationWarning: `env_index` has been deprecated. Use `episode.env_id` instead. This will raise an error in the future!
(pid=2530) 2021-03-29 09:51:14,935	WARNING deprecation.py:33 -- DeprecationWarning: `env_index` has been deprecated. Use `episode.env_id` instead. This will raise an error in the future!
(pid=2528) 2021-03-29 09:51:14,965	WARNING deprecation.py:33 -- DeprecationWarning: `env_index` has been deprecated. Use `episode.env_id` instead. This will raise an error in the future!
(pid=2529) 2021-03-29 09:51:15,023	WARNING deprecation.py:33 -- DeprecationWarning: `env_index` has been deprecated. Use `episode.env_id` instead. This will raise an error in the future!
(pid=2530) GPU available: False, used: False
(pid=2530) TPU available: None, using: 0 TPU cores
(pid=2530) 2021-03-29 09:51:21,161	INFO trainable.py:100 -- Trainable.setup took 10.426 seconds. If your trainable is slow to initialize, consider setting r

(pid=2529) --------------------------------------------------------------------------------
(pid=2529) DATALOADER:0 TEST RESULTS
(pid=2529) {'test/loss': tensor(4.3133),
(pid=2529)  'test/monte_carlo_abs_diff': tensor(19.0811)
(pid=2529) ,
(pid=2529)  'test/monte_carlo_cossim': 
(pid=2529) tensor(0.7554)
(pid=2529) ,
(pid=2529)  'test/monte_carlo_svg_norm': 
(pid=2529) tensor(113.6830),
(pid=2529)  'test/monte_carlo_value'
(pid=2529) : tensor(-1237.1011)
(pid=2529) ,
(pid=2529)  'true_svg_norm': 
(pid=2529) tensor(75.3633),
(pid=2529)  
(pid=2529) 'true_value': 
(pid=2529) tensor(-1218.0200)}
Result for Experiment_6b8f8_00003:
  date: 2021-03-29_09-53-43
  done: true
  experiment_id: 2ab9278011f2452593221e849e96c6eb
  hostname: Angelos-MBP
  iterations_since_restore: 1
  node_ip: 192.168.15.8
  pid: 2529
  test/loss: 4.313302516937256
  test/monte_carlo_abs_diff: 19.0810546875
  test/monte_carlo_cossim: 0.7554446458816528
  test/monte_carlo_svg_norm: 113.68297576904297
  test/monte_car

(pid=2668) 2021-03-29 09:53:58,035	WARNING deprecation.py:33 -- DeprecationWarning: `env_index` has been deprecated. Use `episode.env_id` instead. This will raise an error in the future!


(pid=2530) --------------------------------------------------------------------------------
(pid=2530) DATALOADER:0 TEST RESULTS
Result for Experiment_6b8f8_00001:
  date: 2021-03-29_09-54-03
  done: true
  experiment_id: 7b0856b390e846829f72f928c6f52d2b
  hostname: Angelos-MBP
  iterations_since_restore: 1
  node_ip: 192.168.15.8
  pid: 2530
  test/loss: 9.70977783203125
  test/monte_carlo_abs_diff: 331.280517578125
  test/monte_carlo_cossim: 0.9578627943992615
  test/monte_carlo_svg_norm: 32713.046875
  test/monte_carlo_value: -3065.187744140625
  time_since_restore: 162.70892882347107
  time_this_iter_s: 162.70892882347107
  time_total_s: 162.70892882347107
  timestamp: 1617022443
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: 6b8f8_00001
  true_svg_norm: 28296.2109375
  true_value: -2733.9072265625
  


(pid=2530) {'test/loss': tensor(9.7098),
(pid=2530)  'test/monte_carlo_abs_diff': tensor(331.2805),
(pid=2530)  'test/monte_carlo_cossim': tensor(0.9579),
(pid=2530)  'test/monte_carlo_svg_norm': tensor(32713.0469),
(pid=2530)  'test/monte_carlo_value': tensor(-3065.1877),
(pid=2530)  'true_svg_norm': tensor(28296.2109),
(pid=2530)  'true_value': tensor(-2733.9072)}
(pid=2530) --------------------------------------------------------------------------------


...

2021-03-29 16:25:01,303	ERROR trial_runner.py:616 -- Trial Experiment_6b8f8_00255: Error processing event.
Traceback (most recent call last):
  File "/Users/angelolovatto/Library/Caches/pypoetry/virtualenvs/lqsvg-kEsPsxvA-py3.8/lib/python3.8/site-packages/ray/tune/trial_runner.py", line 586, in _process_trial
    results = self.trial_executor.fetch_result(trial)
  File "/Users/angelolovatto/Library/Caches/pypoetry/virtualenvs/lqsvg-kEsPsxvA-py3.8/lib/python3.8/site-packages/ray/tune/ray_trial_executor.py", line 609, in fetch_result
    result = ray.get(trial_future[0], timeout=DEFAULT_GET_TIMEOUT)
  File "/Users/angelolovatto/Library/Caches/pypoetry/virtualenvs/lqsvg-kEsPsxvA-py3.8/lib/python3.8/site-packages/ray/_private/client_mode_hook.py", line 47, in wrapper
    return func(*args, **kwargs)
  File "/Users/angelolovatto/Library/Caches/pypoetry/virtualenvs/lqsvg-kEsPsxvA-py3.8/lib/python3.8/site-packages/ray/worker.py", line 1456, in get
    raise value.as_instanceof_cause()
ray.exc

Result for Experiment_6b8f8_00255:
  {}
  


2021-03-29 16:25:03,890	ERROR trial_runner.py:616 -- Trial Experiment_6b8f8_00254: Error processing event.
Traceback (most recent call last):
  File "/Users/angelolovatto/Library/Caches/pypoetry/virtualenvs/lqsvg-kEsPsxvA-py3.8/lib/python3.8/site-packages/ray/tune/trial_runner.py", line 586, in _process_trial
    results = self.trial_executor.fetch_result(trial)
  File "/Users/angelolovatto/Library/Caches/pypoetry/virtualenvs/lqsvg-kEsPsxvA-py3.8/lib/python3.8/site-packages/ray/tune/ray_trial_executor.py", line 609, in fetch_result
    result = ray.get(trial_future[0], timeout=DEFAULT_GET_TIMEOUT)
  File "/Users/angelolovatto/Library/Caches/pypoetry/virtualenvs/lqsvg-kEsPsxvA-py3.8/lib/python3.8/site-packages/ray/_private/client_mode_hook.py", line 47, in wrapper
    return func(*args, **kwargs)
  File "/Users/angelolovatto/Library/Caches/pypoetry/virtualenvs/lqsvg-kEsPsxvA-py3.8/lib/python3.8/site-packages/ray/worker.py", line 1456, in get
    raise value.as_instanceof_cause()
ray.exc

Result for Experiment_6b8f8_00254:
  {}
  


TuneError: ('Trials did not complete', [Experiment_6b8f8_00019, Experiment_6b8f8_00023, Experiment_6b8f8_00046, Experiment_6b8f8_00056, Experiment_6b8f8_00062, Experiment_6b8f8_00068, Experiment_6b8f8_00072, Experiment_6b8f8_00091, Experiment_6b8f8_00100, Experiment_6b8f8_00114, Experiment_6b8f8_00126, Experiment_6b8f8_00134, Experiment_6b8f8_00146, Experiment_6b8f8_00167, Experiment_6b8f8_00174, Experiment_6b8f8_00203, Experiment_6b8f8_00204, Experiment_6b8f8_00205, Experiment_6b8f8_00206, Experiment_6b8f8_00207, Experiment_6b8f8_00208, Experiment_6b8f8_00209, Experiment_6b8f8_00210, Experiment_6b8f8_00211, Experiment_6b8f8_00212, Experiment_6b8f8_00213, Experiment_6b8f8_00214, Experiment_6b8f8_00215, Experiment_6b8f8_00216, Experiment_6b8f8_00217, Experiment_6b8f8_00218, Experiment_6b8f8_00219, Experiment_6b8f8_00220, Experiment_6b8f8_00221, Experiment_6b8f8_00222, Experiment_6b8f8_00223, Experiment_6b8f8_00224, Experiment_6b8f8_00225, Experiment_6b8f8_00226, Experiment_6b8f8_00227, 

In [5]:
ray.shutdown()

In [ ]:
!wandb sync --sync-all

Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/hdjnszks ...done.
Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/1odoecgx ...done.
Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/tpx8igac ...done.
Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/34nstzcx ...done.
Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/2odel87p ...done.
Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/15px4148 ...done.
Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/1omb432h ...done.
Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/vb45pbfh ...done.
Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/13xwcuqi ...done.
Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/1d6nexfq ...done.
Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/1jyekbot ...done.
Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/2zbtnfpl ...done.
Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/2fsamodo ...done.
Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/1vn6klcy ...done.
Syncing: https://wandb.ai/angelovtt/LQG-SVG/runs/3sh6sjel ...d